In [ ]:
# import modules
import sys, time, random, yaml
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
from tqdm.rich import tqdm
import seaborn as sns
from matplotlib.ticker import FormatStrFormatter
import matplotlib.ticker as ticker
from collections import Counter
import plotly.graph_objects as go
import plotly.io as pio

# Set up plot defaults
import matplotlib as mpl
mpl.rcParams['figure.figsize'] = 14.0,10.0  # Roughly 11 cm wde by 8 cm high
mpl.rcParams['font.size'] = 20.0 # Use 14 point font
sns.set(style="whitegrid")

font_size = {
    "xlabel": 17,
    "ylabel": 17,
    "xticks": 15,
    "yticks": 15,
    "legend": 13,
    "title": 13,
}

plt.rcParams.update({
    "axes.labelsize": font_size["xlabel"],  # X and Y axis labels
    "xtick.labelsize": font_size["xticks"],  # X ticks
    "ytick.labelsize": font_size["yticks"],  # Y ticks
    "legend.fontsize": font_size["legend"]  # Legend
})

# loading the yaml file
with open('metadata.key_variables.arm.yml', 'r') as file:
    yml = yaml.safe_load(file)

In [69]:
fontfamily = "Open Sans"
dataset = 'SRS'

data = yml['NSA']['C1'][dataset]
vars = data['var_name']
title = data['title']
filename = data['filename']

# Data Preparation
df = pd.read_csv(f"../data/{filename}", usecols=vars)
df[vars[0]] = pd.to_datetime(df[vars[0]])
df = df.set_index(vars[0])
df = df.resample("10T").mean().dropna().reset_index()
df['week'] = (df[vars[0]] - df[vars[0]].min()).dt.days // 7 + 1

groups = {
    "Air Temperature": [v for v in vars if "air_temperature" in v and v != vars[0]],
    "Distance": [v for v in vars if "distance_" in v],
    "Data Quality": [v for v in vars if "data_quality_" in v],
}

trace_meta = {}
figs = {}

for group_name, group_vars in groups.items():
    fig = go.Figure()
    trace_meta[group_name] = []

    for var in group_vars:
        for week in range(1, 5):
            df_week = df[df['week'] == week]
            trace = go.Scattergl(
                x=df_week[vars[0]],
                y=df_week[var],
                mode='lines',
                name=f"{var} (Week {week})",
                visible=(week == 1)
            )
            fig.add_trace(trace)
            trace_meta[group_name].append(week)

    fig.update_layout(
        paper_bgcolor='#B5828C', 
        title=dict(text=f"{title} - {group_name} (Week 1)",
                    font=dict(color='#EBFDFB', size=26, family=fontfamily)),
        xaxis=dict(title=dict(text=vars[0], font=dict(color='#EBFDFB', size=20, family=fontfamily)),
                   tickfont=dict(color='#EBFDFB', size=13.5, family=fontfamily)),
        yaxis=dict(title=dict(text=group_name, font=dict(color='#EBFDFB', size=20, family=fontfamily)),
                   tickfont=dict(color='#EBFDFB', size=13.5, family=fontfamily)),
        legend=dict(
            x=1.02, y=1, yanchor='top',
            # bordercolor="white", borderwidth=1,
            font=dict(color='#EBFDFB', size=15, family=fontfamily)
        ),
        updatemenus=[dict(
            type="dropdown",
            direction="down",
            showactive=True,
            x=1.02,
            y=1.1,
            xanchor="left",
            yanchor="top",
            font=dict(color="lightgrey", size=15, family=fontfamily),
            buttons=[
                dict(
                    label=f"Week {w}",
                    method="update",
                    args=[
                        {"visible": [t == w for t in trace_meta[group_name]]},
                        {"title": f"{title} - {group_name} (Week {w})"}
                    ],
                )
                for w in range(1, 5)
            ]
        )],
        height=800
    )

    figs[group_name] = fig
    fig.show()

html_blocks = []
for i, (name, fig) in enumerate(figs.items()):
    fig_html = pio.to_html(fig, include_plotlyjs=('cdn' if i == 0 else False), full_html=False)
    block = f"""
    <div style="display: flex; justify-content: center; margin-top: 20px;">
        <div id="{name.replace(' ', '_').lower()}_container" style="width: 90%;">
            {fig_html}
        </div>
    </div>
    """
    html_blocks.append(block)

full_html = f"""
<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>SRS Plotly Plots</title>
    <link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/font-awesome/6.5.0/css/all.min.css">
    <link rel="stylesheet" href="/style.css">
    <script src="https://cdn.plot.ly/plotly-latest.min.js"></script>
</head>
<body>
    <h1>SRS Plotly Plots</h1>

    <nav id="cut-nav"> 
        <ul id="cut-links">
            <li><a href="SRS.html" class="active">SRS</a></li>
            <li><a href="LPM.html">LPM</a></li>
            <li><a href="SPMF.html">SPMF</a></li>
            <li><a href="SONIC.html">SONIC</a></li>
        </ul>
    </nav>

    <!-- performance or selection plots -->
    <nav id="mode-nav">
    </nav>

    <!-- Section to display images -->
    <section>
        <h2 id="cut-title">{title} Description<br>
            Can drag to zoom in & double click to reset below images
        </h2>
        <div class="wrapper" id="image-container">
            <!-- Images will be dynamically added here -->
        </div>
    </section>

    <!-- Modal for Fullscreen Image -->
    <div id="image-modal" class="modal">
        <span class="close">&times;</span>
        <img class="modal-content" id="modal-img">
    </div>


    <!-- Sidebar -->
    <div id="sidebar">
    <h3>Test Plots</h3>
    <ul>
        <li><a href="../index.html#main" id="main-btn">main</a></li>
        <li><a href="SRS.html" id="test-btn">SRS</a></li>
        <li><a href="LPM.html" id="test-btn">LPM</a></li>
        <li><a href="SPMF.html" id="test-btn">SPMF</a></li>
        <li><a href="SONIC.html" id="test-btn">SONIC</a></li>
    </ul>
    </div>

    <div id="sidebar-toggle"><i class="fas fa-angle-right"></i></div>

    <!-- Plotly Graphs -->
  {''.join(html_blocks)}
    <script src="/sidebar.js"></script>


</body>
</html>
"""

# Save to file
with open("tmp1.html", "w", encoding="utf-8") as f:
    f.write(full_html)

In [72]:
fontfamily = "Open Sans"
dataset = 'SPMF'

data = yml['NSA']['C1'][dataset]
vars = data['var_name']
title = data['title']
filename = data['filename']

# Data Preparation
df = pd.read_csv(f"../data/{filename}", usecols=vars)
df[vars[0]] = pd.to_datetime(df[vars[0]])
df = df.set_index(vars[0])
df = df.resample("10T").mean().dropna().reset_index()
df['week'] = (df[vars[0]] - df[vars[0]].min()).dt.days // 7 + 1

trace_meta = {}
figs = {}

for var in vars[1:]:
    fig = go.Figure()
    trace_meta[var] = []

    for week in range(1, 5):
        df_week = df[df['week'] == week]
        trace = go.Scattergl(
            x=df_week[vars[0]],
            y=df_week[var],
            mode='lines',
            name=f"{var} (Week {week})",
            visible=(week==1),
            showlegend=True,
            line=dict(color="#55AD9B")
        )
        fig.add_trace(trace)

    fig.update_layout(
        paper_bgcolor='#B5828C', 
        # plot_bgcolor='#B5828C',
        title=dict(text=f"{title} - {var} (Week 1)",
                    font=dict(color='#EBFDFB', size=26, family=fontfamily)),
        xaxis=dict(title=dict(text=vars[0], font=dict(color='#EBFDFB', size=20, family=fontfamily)),
                   tickfont=dict(color='#EBFDFB', size=13.5, family=fontfamily)),
        yaxis=dict(title=dict(text=var, font=dict(color='#EBFDFB', size=20, family=fontfamily)),
                   tickfont=dict(color='#EBFDFB', size=13.5, family=fontfamily)),
        legend=dict(
            x=1.02, y=1, yanchor='top',
            # bordercolor="white", borderwidth=1,
            font=dict(color='#EBFDFB', size=15, family=fontfamily)
        ),
        updatemenus=[dict(
            type="dropdown",
            direction="down",
            showactive=True,
            x=1.02,
            y=1.1,
            xanchor="left",
            yanchor="top",
            font=dict(color="lightgrey", size=15, family=fontfamily),
            buttons=[
                dict(
                    label=f"Week {w}",
                    method="update",
                    args=[
                        {"visible": [i == w-1 for i in range(4)]},
                        {"title": f"{title} - {var} (Week {w})"}
                    ]
                )
                for w in range(1, 5)
            ]
        )],
        height=800
    )

    figs[var] = fig
    fig.show()  # Show each plot inline


# Save all figures into a single HTML with flex containers
html_blocks = []
for i, (name, fig) in enumerate(figs.items()):
    fig_html = pio.to_html(fig, include_plotlyjs=('cdn' if i == 0 else False), full_html=False)
    block = f"""
    <div style="display: flex; justify-content: center; margin-top: 20px;">
        <div id="{name.replace(' ', '_').lower()}_container" style="width: 90%;">
            {fig_html}
        </div>
    </div>
    """
    html_blocks.append(block)

# Combine all into one HTML document
full_html = f"""
<!DOCTYPE html>
<html lang="en">
<head>
    <meta charset="UTF-8">
    <meta name="viewport" content="width=device-width, initial-scale=1.0">
    <title>{data['title']} Plotly Plots</title>
    <link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/font-awesome/6.5.0/css/all.min.css">
    <link rel="stylesheet" href="/style.css">
    <script src="https://cdn.plot.ly/plotly-latest.min.js"></script>
</head>
<body>
    <h1>{data['title']} ({dataset}) Plotly Plots</h1>

    <nav id="cut-nav"> 
        <ul id="cut-links">
            <li><a href="SRS.html" class="active">SRS</a></li>
            <li><a href="LPM.html">LPM</a></li>
            <li><a href="SPMF.html">SPMF</a></li>
            <li><a href="SONIC.html">SONIC</a></li>
        </ul>
    </nav>

    <!-- performance or selection plots -->
    <nav id="mode-nav">
    </nav>

    <!-- Section to display images -->
    <section>
        <h2 id="cut-title">{title} Description<br>
            Can drag to zoom in & double click to reset below images
        </h2>
        <div class="wrapper" id="image-container">
            <!-- Images will be dynamically added here -->
        </div>
    </section>

    <!-- Modal for Fullscreen Image -->
    <div id="image-modal" class="modal">
        <span class="close">&times;</span>
        <img class="modal-content" id="modal-img">
    </div>


    <!-- Sidebar -->
    <div id="sidebar">
    <h3>Test Plots</h3>
    <ul>
        <li><a href="../index.html#main" id="main-btn">main</a></li>
        <li><a href="SRS.html" id="test-btn">SRS</a></li>
        <li><a href="LPM.html" id="test-btn">LPM</a></li>
        <li><a href="SPMF.html" id="test-btn">SPMF</a></li>
        <li><a href="SONIC.html" id="test-btn">SONIC</a></li>
    </ul>
    </div>

    <div id="sidebar-toggle"><i class="fas fa-angle-right"></i></div>

    <!-- Plotly Graphs -->
  {''.join(html_blocks)}
    <script src="/sidebar.js"></script>


</body>
</html>
"""

# Save to file
with open("tmp1.html", "w", encoding="utf-8") as f:
    f.write(full_html)

In [ ]:
# re-save the csv to itself with only the specified columns

datasets = yml['NSA']['C1']

for dataset_name, config in datasets.items():
    filename = config['filename']
    var_list = config['var_name']

    try:
        # Load only the specified columns
        df = pd.read_csv(f"../data/{filename}", usecols=var_list)

        # Save back (overwrite)
        df.to_csv(f"../data2/{filename}", index=False)
        print(f"✅ Trimmed and saved: {filename}")

    except Exception as e:
        print(f"❌ Failed to process {filename}: {e}")


✅ Trimmed and saved: nsasrsC1.a1_snowyear_2025_trimmed.csv
✅ Trimmed and saved: nsalpmC1.a1_snowyear_2025_trimmed.csv
✅ Trimmed and saved: nsaspmfC1.a1_snowyear_2025_trimmed.csv
✅ Trimmed and saved: nsasonicwind3dC1.a1_snowyear_2025_trimmed.csv
